In [8]:
from __future__ import print_function
import matplotlib.pyplot as plt # librairie de plot
from ipywidgets import interact, interactive, fixed, interact_manual, interactive_output
import ipywidgets as widgets
import numpy as np
import scipy as sp
import seaborn as sns
from scipy.interpolate import griddata
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

 # Kinetic Relaxation scheme
 
In this notebook we propose to introduce the **kinetic Relaxation schemes** for hyperbolic system. It is a generic way to solve hyperbolic systems at first/second order without CFL condition. This methos is a generalization of **Lattice  Boltzmann method**.

## General principle

We want to solve the hyperbolic equation

$$
\partial_t \mathbf{U} + \partial_x \mathbf{F}(\mathbf{U})=0
$$

with $\mathbf{U}$ a vector function of size $N$ and the speeds of ths system are given by $\partial_{\mathbf{U}} \mathbf{F}$. The Idea consis to appromixate this system by a **larger one** simpler to solve. We speak about **relaxation**.

We introduce $\mathbf{f}$ a vector function of size $n_v>N$. The **kinetic relaxation system** is given by 

$$
\partial_t \mathbf{f} + \Lambda \partial_x \mathbf{f}= \frac{1}{\epsilon}(\mathbf{f}^{eq}(\mathbf{U})-\mathbf{f})
$$

with $\Lambda$ a diagonal constant matrix.

**Definition 1.1**:
- the  **kinetic variables**: the vector function $\mathbf{f}$,
- the **moment matrix**: P a constant matrix,
- the **kinetic velocities**: the values of the diagonal of $\Lambda$,
- the **relaxation parameter**: a small parameter $0\leq \epsilon< 1$.
- the **equilibrium**: the vector function $\mathbf{f}^{eq}(\mathbf{U})$ which depend only of the original variables.

With all these ingrediants it is possible to prove formally that the **kinetic relaxation system** is an approximation of the original hyperbolic model on some conditions.

**Lemma 1.1 (Approximation)**:

   if $P\mathbf{f}=P\mathbf{f}^{eq}=\mathbf{U}$ and $P\Lambda \mathbf{f}^{eq}=\mathbf{F}(\mathbf{U})$ we can approximate at the limit $\epsilon$ tends to zero the **Kinetic relaxation system** by
   
   $$
   \partial_t \mathbf{U} + \partial_x \mathbf{F}(\mathbf{U})=O(\epsilon)
   $$
   
*Proof:*
We make a Chapman-Enskog extansion like: $\mathbf{f}=\mathbf{f}_0+\epsilon\mathbf{f}_1+O(\epsilon^2)$
    
- Term in $\frac{1}{\epsilon}$:

    $$
    \mathbf{f}^{eq,0}(\mathbf{U})-\mathbf{f}^0=0
    $$

- Term in $O(1)$:

    $$
    \partial_t \mathbf{f}^0 + \Lambda \partial_x \mathbf{f}^0= (\mathbf{f}^{eq,1}(\mathbf{U})-\mathbf{f}^1)
    $$
    
     using the previous relation and the fact that $\Lambda$ is constant we obtain 
     
     $$
    \partial_t \mathbf{f}^{eq,0} + \partial_x (\Lambda \mathbf{f}^{eq,0})= (\mathbf{f}^{eq,1}(\mathbf{U})-\mathbf{f}^1)
    $$
    
    Now we multiply by $P$ and use that this matrix is also constant
    
     $$
    \partial_t P\mathbf{f}^{eq,0} + \partial_x (P\Lambda \mathbf{f}^{eq,0})= (P\mathbf{f}^{eq,1}(\mathbf{U})-P\mathbf{f}^1)
    $$
    
    To conclude we use the asusmptions which gives that
    
     $$
    \partial_t \mathbf{U}^{0} + \partial_x (\mathbf{F}(\mathbf{U}^{0}))= 0
    $$
    
    and we use that $\mathbf{U}=\mathbf{U}^0+O(\epsilon)$ to obtain the final result.
    
*end Proof*

## Discretization

The discretization of the **kinetic relaxation system** is simple. The first consist to **split** the resolution in of the transport operator and the source term. With this splitting we separate **a nonlocal but linear** part and a **nonlinear but local** part.

- Step 1: $\partial_t \mathbf{f} + \Lambda \partial_x \mathbf{f}= 0$
- Step 2: $\partial_t \mathbf{f} = \frac{1}{\epsilon}(\mathbf{f}^{eq}(\mathbf{U})-\mathbf{f})$

To discretize the step one we use a Semi-Lagrangian scheme. We known that 

$$
f_i(t+\Delta t,x)=f(t,x-\Lambda_i \Delta t), \quad \forall i\leq n_v
$$

using the characteristic formula. Since $x-\Lambda_i \Delta t$ is not a mesh point in general. We replace this formula by

$$
f_i(t+\Delta t,x)=I_{f_i}(t,x-\Lambda_i \Delta t), \quad \forall i\leq n_v
$$

with $I_{f_i}(x)$ an polynomial interpolation of the function $f_i$.

For the step two we use an $\theta$ implicit scheme. We obtain

$$
\frac{\mathbf{f}^{n+1}-\mathbf{f}^{n}}{\Delta t}= \theta (\mathbf{f}^{eq}(\mathbf{U}^{n+1})-\mathbf{f}^{n+1}) + (1-\theta) (\mathbf{f}^{eq}(\mathbf{U}^{n})-\mathbf{f}^{n})
$$

However, using the assumption which assure the convergence $P\mathbf{f}=P\mathbf{f}^{eq}=\mathbf{U}$ we obtain that

$$
\partial_t P \mathbf{f}=\partial_t \mathbf{U}=0
$$

in the second step. So we have

$$
\frac{\mathbf{f}^{n+1}-\mathbf{f}^{n}}{\Delta t}= \mathbf{f}^{eq}(\mathbf{U}^{n+1})  - \theta \mathbf{f}^{n+1}- (1-\theta) \mathbf{f}^{n}
$$

reformulating the previous time scheme to obtain

$$
\mathbf{f}^{n+1} = \omega \mathbf{f}^{eq}(\mathbf{U}^n)+(1-\omega)\mathbf{f}^n
$$

with $\omega=\frac{\Delta t}{\epsilon + \theta \Delta t}$.

**Definition 1.2 (Final scheme)**:

   - Transport step:
   
    $$
    f_i(t+\Delta t,x)=I_{f_i}(t,x-\Lambda_i \Delta t), \quad \forall i\leq n_v
    $$
   
   - Relaxation step:
   
   $$
    \mathbf{f}^{n+1} = \omega \mathbf{f}^{eq}(\mathbf{U}^*)+(1-\omega)\mathbf{f}^*
    $$

In [27]:
#### Solver
def create_velocities(t_vel,q,lamb):
    if q == 2: 
        t_vel[0] = -1.0*lamb
        t_vel[1] = 1.0*lamb
    if q == 3: 
        t_vel[0] = -1.0*lamb 
        t_vel[1] = 0.0 
        t_vel[2] = 1.0*lamb 

def Solver (model="Burgers", lattice="q2", test="Gaussian" , Nx=100, order="linear", dt=0.001, lamb=1.5, \
            xl=-1.0, xr=1.0, nt_max=100, nplot=0, omega=1.0):
    
    p = np.linspace(xl,xr,Nx)     
    tplot= np.linspace(0.0,nt_max*dt,nplot+2)
    
    N,f_feq,f_plot = define_model(model,lattice)
    nl,nv, tab_q,f_mom = define_lattice(N,lattice)    
    f_init,f_bc  = define_test(model,test) 
    bl_u = f_bc(-1)
    br_u = f_bc(1)
    
    bc_f = np.zeros(nv)  
    u = f_init(p,0.0)
    ax = defplot(N)
       
    t_vel = [[0 for j in range(tab_q[i])] for i in range(nl) ]  
    for i in range(0,nl):
        create_velocities(t_vel[i],tab_q[i],lamb) 
        
    t_f =np.zeros((nv,Nx))
    t_fnew =np.zeros((nv,Nx))
    t_f = f_feq(N,tab_q,u,t_vel)
    bl_f = f_feq(N,tab_q,bl_u,t_vel)
    br_f = f_feq(N,tab_q,br_u,t_vel)
    nt = 0; ti = 0; 
    time = 0.0
    while nt < nt_max:

    # transport     
        for i in range(nl):
            for j in range(tab_q[i]):
                v = t_vel[i][j]
                i_f = i * tab_q[i] + j 

                x1 = p[:]-v*dt
                if v>0: 
                    bc = bl_f[i_f]
                else: 
                    bc = br_f[i_f]
                t_fnew[i_f] = griddata(p, t_f[i_f], (x1), method=order,fill_value=bc)               
                
    #### relaxation
        u = f_mom(Nx,N,t_vel,t_fnew)
        for k in range(0,nv):
            t_f[k] = t_fnew[k] + omega*(f_feq(N,tab_q,u,t_vel)[k] - t_fnew[k]) 
        
        if time >= tplot[ti] and time <tplot[ti]+dt:
                f_plot(ax,p,u)
                pinit=0
                ti =ti+1
                
        nt = nt +1
        time = time +dt  
    
    u = f_mom(Nx,N,t_vel,t_f)
    f_plot(ax,p,u)
    plt.show()
    

#### generic
def moment_d1q2 (Nx,N,t_vel,f): # relation entre u et les f
    u = []
    for i in range(0,N):
        uloc = f[i*2]+f[i*2+1]
        u.append(uloc)
    return u

def moment_d1q3n1 (Nx,N,t_vel,f): 
    u = [] 
    uloc = f[0]+f[1]+f[2]
    u.append(uloc)
    uloc = t_vel[0][0]*f[0]+t_vel[0][1]*f[1]+t_vel[0][2]*f[2]
    u.append(uloc)
    return u

def define_model(model,lattice):
    if model == "EulerIso":
        N =2
        fl_plot = plot_EulerIso     
        if lattice == "q2":
            fl_feq = feq_EulerIso_d1q2n2
        if lattice == "q3n1":
            fl_feq = feq_EulerIso_d1q3n1
    
    if model == "Burgers":
        N=1
        fl_plot = plot_Burgers    
        if lattice == "q2":
            fl_feq = feq_Burgers_d1q2n1
    
    if model == "Euler":
        N =3
        fl_plot = plot_Euler    
        if lattice == "q2":
            fl_feq = feq_EulerIso_d1q2n3
            
    return N,fl_feq,fl_plot

def define_test(model,test):
    if model == "EulerIso":    
        if test == "Riemann":
            fl_init = EulerIso_Riemann
            fl_bc = bc_EulerIso_Riemann
        if test == "Waves":
            fl_init = EulerIso_Waves
            fl_bc = bc_EulerIso_Waves
    
    if model == "Burgers":
        if test == "Gaussian":
            fl_init = Burgers_Gaussian
            fl_bc = bc_Burgers_Gaussian
        if test == "Shock":
            fl_init = Burgers_Shock
            fl_bc = bc_Burgers_Shock
        if test == "Rarefaction":
            fl_init = Burgers_Rarefaction
            fl_bc = bc_Burgers_Rarefaction
            
    if model == "Euler":    
        if test == "Sod":
            fl_init = Euler_Sod
            fl_bc = bc_Euler_Sod
        if test == "Waves":
            fl_init = Euler_Waves
            fl_bc = bc_Euler_Waves
    
            
    return fl_init,fl_bc

def define_lattice(N,lattice):
    if lattice == "q2":  
        nv = N*2
        tab_q = np.ones(N,dtype=int)*2
        f_mom = moment_d1q2
        nl = N
    if lattice == "q3n1":  
        nv = 3
        tab_q = [3]
        f_mom = moment_d1q3n1
        nl = 1
        
    return nl,nv,tab_q,f_mom

def defplot(N):
    ax = []
    if N==1:
        fig=plt.figure(figsize=(6,4))
        ax.append(fig.add_subplot(111))
       
    if N==2:
        fig=plt.figure(figsize=(12,4))
        ax.append(fig.add_subplot(121))
        ax.append(fig.add_subplot(122))
    
    if N>2 and N <=4:
        fig=plt.figure(figsize=(12,6))
        ax.append(fig.add_subplot(221))
        ax.append(fig.add_subplot(222))
        ax.append(fig.add_subplot(223))
        ax.append(fig.add_subplot(224))
    sns.set_palette("Spectral",10)
    return ax


## Models

### Burgers equation

The model considered is the Burgers equation:

$$
\partial_t \rho + \partial_x \left( \frac{\rho^2}{2}\right)=0
$$

We solve this with the $D1Q2$ model. In this case the **kinetic relaxation system** is given by

$$
P=\left(\begin{array}{cc} 1 & 1\end{array}\right), \quad \mathbf{f}=\left(\begin{array}{c} f_{-} \\ f_{+}\end{array}\right), \quad \Lambda=\left(\begin{array}{cc} -\lambda& 0 \\ 0 & \lambda\end{array}\right), \quad \mathbf{f}^{eq}=\left(\begin{array}{c} \frac{\rho}{2} - \frac{\rho^2}{4\lambda} \\ \frac{\rho}{2} + \frac{\rho^2}{4\lambda}\end{array}\right) 
$$

In [28]:
####  Burgers 
def Burgers_Gaussian (x,t):
    sig = 0.02
    ax = 1.0
    x0 = ax*t
    values= np.exp(-((x-x0)**2.0)/sig)
    return [values]

def Burgers_Shock (x,t):
    values = 1.0 - 0.5*np.heaviside(x,1.0)
    return [values]

def Burgers_Rarefaction (x,t):
    values = 0.5*np.heaviside(x,1.0)
    return [values]

def feq_Burgers_d1q2n1(N,tab_q,u,t_vel): # feq en fonction de u et g(u)
    f = []
    c= abs(t_vel[0][0])
    floc = 0.5*u[0]-0.5*(0.5*u[0]*u[0])/c
    f.append(floc)
    c= abs(t_vel[0][1])
    floc = 0.5*u[0]+0.5*(0.5*u[0]*u[0])/c
    f.append(floc)
    return f 

def plot_Burgers(ax,p,u):
    ax[0].plot(p,u[0],linewidth=3,linestyle='dashed')
       
def bc_Burgers_Gaussian(k):
    return [0.0]

def bc_Burgers_Shock(k):
    if k== -1:
        return [1.0 ,0.0]
    else:
        return [0.5 ,0.0]
    
def bc_Burgers_Rarefaction(k):
    if k== -1:
        return [0.0 ,0.0]
    else:
        return [0.5 ,0.0]

### Isothermal Euler equation

The model considered is the isothermal Euler equation:

$$
\left\{\begin{array}{l}
\partial_t \rho + \partial_x \left( \rho u\right)=0\\
\partial_t \rho u + \partial_x \left( \rho u^2 + c^2 \rho\right)=0\\
\end{array}\right.
$$

The first possibility is the $D1Q2n2$ model. In this case the **kinetic relaxation system** is given by

$$
P=\left(\begin{array}{cccc} 1 & 1 & 0 & 0\\ 0& 0 & 1 & 1\end{array}\right), \quad \mathbf{f}=\left(\begin{array}{c} f_{r}^{-} \\ f_{r}^{+} \\ f_{ru}^{-} \\ f_{ru}^{+}\end{array}\right), \quad \Lambda=\left(\begin{array}{cccc} -\lambda& 0  & 0 & 0\\ 0 & \lambda & 0 & 0 \\ 0 &0 &-\lambda& 0 \\ 0& 0 &0 & \lambda\end{array}\right), \quad \mathbf{f}^{eq}=\left(\begin{array}{l} \frac{\rho}{2} - \frac{\rho u}{2\lambda} \\ \frac{\rho}{2} + \frac{\rho u}{2\lambda} \\  \frac{\rho u}{2} - \frac{\rho u^2 + c^2 \rho}{2\lambda} \\ \frac{\rho}{2} + \frac{\rho u^2 + c^2 \rho}{2\lambda}\end{array}\right) 
$$

The second possibility is the $D1Q3$ model. In this case the **kinetic relaxation system** is given by

$$
P=\left(\begin{array}{cccc} 1 & 1 & 1\\ -\lambda& 0 & \lambda\end{array}\right), \quad \mathbf{f}=\left(\begin{array}{c} f^{-} \\ f^{0} \\ f^{+}\end{array}\right), \quad \Lambda=\left(\begin{array}{ccc} -\lambda& 0  & 0 \\ 0 & 0 & 0 \\ 0 &0 &\lambda \end{array}\right), \quad \mathbf{f}^{eq}=\left(\begin{array}{l} \frac{1}{2\lambda^2}(\rho u (u-\lambda) +c^2\rho) \\ \frac{\rho}{\lambda^2}(\lambda^2-u^2-c^2) \\\frac{1}{2\lambda^2}(\rho u (u+\lambda) +c^2\rho) \end{array}\right) 
$$

In [29]:
### Euler isotherme
def EulerIso_Waves(x,t):
    sig = 0.02

    x01 = 0.0
    rho = 0.1+np.exp(-((x-x01)**2.0)/sig)       
    u = 0.0
    return [rho,rho*u]   

def EulerIso_Riemann(x,t):
    
    rho = 1.0 - 0.5*np.heaviside(x,1.0)
    u = 0.0
    return [rho,rho*u] 
    
def feq_EulerIso_d1q2n2(N,tab_q,u,t_vel): # feq en fonction de u et g(u)
    f = []
    c = abs(t_vel[0][0])
    floc = 0.5*u[0]-0.5*(u[1])/c
    f.append(floc)
    floc = 0.5*u[0]+0.5*(u[1])/c
    f.append(floc)
    c = abs(t_vel[1][0])
    floc = 0.5*u[1]-0.5*(u[1]*u[1]/u[0] + u[0])/c
    f.append(floc)
    floc = 0.5*u[1]+0.5*(u[1]*u[1]/u[0]+ u[0])/c
    f.append(floc)
    return f   

def feq_EulerIso_d1q3n1(N,tab_q,u,t_vel): # feq en fonction de u et g(u)
    f = []
    c = 1.0
    lamb = abs(t_vel[0][0])
    floc = 0.5*u[1]*(u[1]/u[0]-lamb)+0.5*u[0]*c*c
    f.append(floc/(lamb*lamb))
    floc= u[0]*(lamb*lamb-c*c-(u[1]/u[0])*(u[1]/u[0]))
    f.append(floc/(lamb*lamb))            
    floc = 0.5*u[1]*(u[1]/u[0]+lamb)+0.5*u[0]*c*c
    f.append(floc/(lamb*lamb))
    return f 

def plot_EulerIso(ax,p,u):
    ax[0].plot(p,u[0],linewidth=3,linestyle='dashed')
    ax[1].plot(p,u[1]/u[0],linewidth=3,linestyle='dashed')
    
def bc_EulerIso_Waves(k):
    return [0.1,0.0]

def bc_EulerIso_Riemann(k):
    if k== -1:
        return [1.0 ,0.0]
    else:
        return [0.5 ,0.0]


### Euler equation

The model considered is the Euler equation:

$$
\left\{\begin{array}{l}
\partial_t \rho + \partial_x \left( \rho u\right)=0\\
\partial_t \rho u + \partial_x \left( \rho u^2 + p\right)=0\\
\partial_t E + \partial_x \left( Eu + pu\right)=0\\
\end{array}\right.
$$

with $p= (\gamma-1)(E-\frac12 \rho u^2)$.

The first possibility is the $D1Q2n3$ model. In this case the **kinetic relaxation system** is given by

$$
P=\left(\begin{array}{cccccc} 1 & 1 & 0 & 0 & 0 & 0\\ 0& 0 & 1 & 1 & 0 & 0\\ 0 & 0 & 0 & 0 & 0 & 0\end{array}\right), \quad \Lambda=\left(\begin{array}{cccccc} -\lambda& 0  & 0 & 0 & 0 & 0\\ 0 & \lambda & 0 & 0 & 0 & 0 \\ 0 &0 &-\lambda& 0 & 0 & 0 \\ 0& 0 &0 & \lambda & 0 & 0 \\ 0 & 0 & 0 & 0& -\lambda & 0 \\ 0 & 0 & 0 & 0 & 0 & \lambda\end{array}\right)
$$

and 

$$
\mathbf{f}=\left(\begin{array}{c} f_{r}^{-} \\ f_{r}^{+} \\ f_{ru}^{-} \\ f_{ru}^{+} \\ f_{E}^{-} \\ f_{E}^{+}\end{array}\right), \quad \mathbf{f}^{eq}=\left(\begin{array}{l} \frac{\rho}{2} - \frac{\rho u}{2\lambda} \\ \frac{\rho}{2} + \frac{\rho u}{2\lambda} \\  \frac{\rho u}{2} - \frac{\rho u^2 + p}{2\lambda} \\ \frac{\rho}{2} + \frac{\rho u^2 + p}{2\lambda} \\  \frac{E}{2} - \frac{Eu + pu}{2\lambda} \\ \frac{E}{2} + \frac{Eu+pu}{2\lambda}\end{array}\right) 
$$

In [38]:
### Euler isotherme
def p_to_E(r,u,p,gamma):
    return r*u*u+p/(gamma-1.0)

def E_to_p(r,ru,E,gamma):
    return (gamma-1.0)*(E-0.5*ru*ru/r)

def Euler_Waves(x,t):
    sig = 0.02
    gamma =3.0
    x01 = 0.0
    rho = 0.1+np.exp(-((x-x01)**2.0)/sig)       
    u = 0.0
    p = 1.0
    return [rho,rho*u,p_to_E(rho,u,p,gamma)]   

def Euler_Sod(x,t):
    gamma =3.0
    rho = 1.0 - 0.875*np.heaviside(x,1.0)
    u = 0.0
    p = 1.0 - 0.9*np.heaviside(x,1.0)
    return [rho,rho*u,p_to_E(rho,u,p,gamma)] 
    
def feq_Euler_d1q2n3(N,tab_q,u,t_vel): # feq en fonction de u et g(u)
    f = []
    lamb = abs(t_vel[0][0])
    gamma= 3.0
    v = u[1]/u[0]
    p = E_to_p(u[0],u[1],u[2],gamma)
    floc = 0.5*u[0]-0.5*(u[1])/lamb
    f.append(floc)
    floc = 0.5*u[0]+0.5*(u[1])/lamb
    f.append(floc)
    floc = 0.5*u[1]-0.5*(u[1]*v + p)/lamb
    f.append(floc)
    floc = 0.5*u[1]+0.5*(u[1]*v+ p)/lamb
    f.append(floc)
    floc = 0.5*u[2]-0.5*(u[2]*v + p*v)/lamb
    f.append(floc)
    floc = 0.5*u[2]+0.5*(u[2]*v + p*v)/lamb
    f.append(floc)
    return f   
def plot_Euler(ax,p,u):
    gamma= 3.0
    ax[0].plot(p,u[0],linewidth=3,linestyle='dashed')
    ax[1].plot(p,u[1]/u[0],linewidth=3,linestyle='dashed')
    ax[2].plot(p,E_to_p(u[0],u[1],u[2],gamma),linewidth=3,linestyle='dashed')
    
def bc_Euler_Waves(k):
    return [0.0,0.0,0.0]

def bc_Euler_Sod(k):
    gamma=3.0
    if k== -1:
        return [1.0 ,0.0,p_to_E(1.0,0.0,1.0,gamma)]
    else:
        return [0.125 ,0.0,p_to_E(0.125,0.0,0.1,gamma)]

In [43]:
#### code parameters
dt = widgets.FloatText(value=0.001,description="dt")
nt_max = widgets.IntText(value=10,description="nt_max")
nplot = widgets.IntSlider(value=0,min=0,max=8,description="internal plot")
Nx = widgets.IntText(value=100,description="Nx")
xl = widgets.FloatText(value=-1.0,description="xl")
xr = widgets.FloatText(value=1.0,description="xr")

omega = widgets.FloatSlider(value=1.0,min=0.5,max=2.0,step=0.05,description="omega:")
order = widgets.RadioButtons(options=['linear','cubic'],value='linear',description="order:")
lamb = widgets.FloatText(value=1.5,description="lattice vel:")

model = widgets.RadioButtons(options=['Burgers','EulerIso','Euler'],value='Burgers',description="model:")
lattice = widgets.RadioButtons(options=['q2'],value='q2',description="lattice:")
testBurgers = ["Gaussian", "Shock","Rarefaction"]
test = widgets.RadioButtons(options=testBurgers,description="test:")

def modeltest(change):
    if change.new == "Burgers":
        test.options = testBurgers
    if change.new == "EulerIso":
        test.options=["Riemann","Waves"]
    if change.new == "Euler":
        test.options=["Sod","Waves"]
    
model.observe(modeltest, names='value')

def modellattice(change):
    if change.new == "Burgers":
        lattice.options = ['q2']
    if change.new == "EulerIso":
        lattice.options=["q2","q3n1"]
    if change.new == "Euler":
        lattice.options=["q2"]
           
    
model.observe(modeltest, names='value')
model.observe(modellattice, names='value')

pmodel = widgets.HBox([model,lattice,test])
ptime = widgets.HBox([dt, nt_max, nplot])
pspace = widgets.HBox([Nx, xl, xr])
porder = widgets.HBox([order, omega, lamb])

ui2= widgets.VBox([pmodel,ptime,pspace,porder])
out2 = widgets.interactive_output(Solver, {'model': model, 'lattice': lattice, 'test':test, 'Nx': Nx, \
                                           "order": order, "dt":dt,'lamb': lamb, 'xl': xl, 'xr': xr,\
                                           'nt_max': nt_max, "nplot": nplot, 'omega': omega})

display(ui2, out2)


Output()